In [1]:
import sys
sys.path.append('..')

import pandas as pd
import numpy as np
from utils import *
import nlpcda
import os

from typing import List, Dict

Simbert不能正常使用，除非你安装：bert4keras、tensorflow ，为了安装快捷，没有默认安装.... No module named 'bert4keras'


In [7]:
class DataAugmentation:
    def __init__(self, configs:Dict[str, dict]) -> None:
        self.entity_swap, self.random_del, self.random_swap = None, None, None

        if 'random_entity' in configs.keys():
            self.entity_swap_p = configs['random_entity'].pop('prop')
            self.entity_swap = nlpcda.Similarword(**(configs['random_entity']))
        if 'random_delete_char' in configs.keys():
            self.random_del_p = configs['random_delete_char'].pop('prop')
            self.random_del = nlpcda.RandomDeleteChar(**(configs['random_delete_char']))
        if 'random_swap' in configs.keys():
            self.random_swap_p = configs['random_swap'].pop('prop')
            self.random_swap = nlpcda.Similarword(**(configs['random_swap']))

    def aug(self, df_full:pd.DataFrame, permute=True, seed=1024) -> pd.DataFrame:
        df = df_full[df_full.label == 1]
        df_neg = df_full[df_full.label == 0]

        L = len(df)
        if self.entity_swap:
            augmented_df = self.aug_single(df, L, self.entity_swap_p, self.entity_swap)
        if self.random_del:
            augmented_df = self.aug_single(augmented_df, L, self.random_del_p, self.random_del)
        if self.random_swap:
            augmented_df = self.aug_single(augmented_df, L, self.random_swap_p, self.random_swap)

        augmented_df = pd.concat((df_neg, augmented_df))
        # ----------------------------------------------
        with pd.option_context('display.max_rows', None, 'display.max_columns', None, ):
            pd.options.display.max_colwidth = 100
            display(augmented_df[-200:])
        # ----------------------------------------------
        if permute:
            augmented_df = augmented_df.sample(frac=1, random_state=seed).reset_index(drop=True)
        return augmented_df

    def aug_single(self, df:pd.DataFrame, L:int, p:float, tool) -> pd.DataFrame:
        """input L: original df length. Avoid augmentation on newly constructed data. """
        idx = np.random.choice(range(L), size=int(L*p))
        slice_df = df.iloc[idx]
        label, text = slice_df[['label', 'text']].values.T
        transformed_slice_df = self.get_transformed_df(slice_df, tool)
        augmented_df = pd.concat((df, transformed_slice_df))
        return augmented_df

    def text_seq_transform(self, tool, texts:List[str]) -> List[str]:
        out = []
        for text in texts:
            transformed_text = tool.replace(text)[-1]
            out.append(transformed_text)
        return np.array(out)
    
    def get_transformed_df(self, slice_df:pd.DataFrame, tool) -> pd.DataFrame:
        label, text = slice_df[['label', 'text']].values.T
        transformed_text = self.text_seq_transform(tool, text)
        # display(text[:10])
        # display(transformed_text[:10])
        transformed_slice_df = slice_df.drop(columns=['text']).copy(deep=True)
        transformed_slice_df['text'] = transformed_text
        return transformed_slice_df
        

In [3]:
np.random.seed(1024)
rnd_idx = np.random.choice(range(1, 43001), size=10000)

train_df = pd.read_csv('../data-org/train.csv', sep='\t')
train_df_slice = pd.read_csv('../data-org/train.csv', sep='\t').iloc[rnd_idx]

train_df.drop(columns=['id'], inplace=True)
train_df_slice.drop(columns=['id'], inplace=True)

In [8]:
entities_file = os.path.join("D:\Apps\Anaconda3\envs\general-torch\Lib\site-packages", "nlpcda\data\entities.txt")

da_configs = {
    'random_entity':{
        'base_file':entities_file, 
        'create_num':2, 
        'change_rate':0.75, 
        'seed':1024, 
        'prop':0.5,  
    }, 
    'random_delete_char':{
        'create_num':2, 
        'change_rate':0.05, 
        'seed':1024, 
        'prop':0.3, 
    }, 
    'random_swap':{
        'create_num':2, 
        'change_rate':0.75, 
        'seed':1024, 
        'prop':0.5, 
    }
}

da = DataAugmentation(da_configs)
train_df_aug = da.aug(train_df)
train_df_slice_aug = da.aug(train_df_slice)

ntf()


load :D:\Apps\Anaconda3\envs\general-torch\Lib\site-packages\nlpcda\data\entities.txt done
load :d:\Apps\Anaconda3\envs\general-torch\lib\site-packages\nlpcda\data\同义词.txt done


label  \
122        1   
32581      1   
31336      1   
25142      1   
17721      1   
33202      1   
12660      1   
13688      1   
36299      1   
30198      1   
3170       1   
7958       1   
19466      1   
40871      1   
29016      1   
16376      1   
23100      1   
33563      1   
34804      1   
26627      1   
40983      1   
24760      1   
549        1   
5910       1   
10091      1   
6931       1   
24809      1   
41829      1   
9908       1   
137        1   
35407      1   
32916      1   
45019      1   
13770      1   
4338       1   
37656      1   
1446       1   
13758      1   
22637      1   
27782      1   
9961       1   
32776      1   
10542      1   
24533      1   
44252      1   
8847       1   
24361      1   
13222      1   
13513      1   
23742      1   
35498      1   
3523       1   
25471      1   
8625       1   
31001      1   
2071       1   
14593      1   
26520      1   
40432      1   
40818      1   
24763      1   
19430      1   
26541      1   
17339      1   
44221      1   
11729      1   
17237      1   
2893       1   
33218      1   
41988      1   
33964      1   
31734      1   
25707      1   
37942      1   
42970      1   
4684       1   
18671      1   
13042      1   
29133      1   
31092      1   
2584       1   
25931      1   
13038      1   
43673      1   
31687      1   
37129      1   
14779      1   
33134      1   
40338      1   
15339      1   
9287       1   
14489      1   
43644      1   
26980      1   
18479      1   
24447      1   
40098      1   
11824      1   
15941      1   
27835      1   
44633      1   
36795      1   
13015      1   
35385      1   
24380      1   
44600      1   
21335      1   
45116      1   
11436      1   
9255       1   
31878      1   
9361       1   
42432      1   
288        1   
27914      1   
8961       1   
15809      1   
6093       1   
18450      1   
44984      1   
38680      1   
44983      1   
27240      1   
30704      1   
8890       1   
25470      1   
26858      1   
11822      1   
21118      1   
24715      1   
10274      1   
19835      1   
14050      1   
82         1   
23664      1   
32508      1   
16294      1   
7594       1   
9901       1   
10692      1   
22487      1   
8626       1   
12452      1   
18676      1   
9591       1   
19509      1   
38265      1   
40533      1   
43146      1   
18529      1   
23856      1   
32375      1   
11339      1   
35102      1   
3680       1   
18761      1   
38753      1   
39885      1   
900        1   
42791      1   
44754      1   
41217      1   
33186      1   
39046      1   
41315      1   
958        1   
27912      1   
25200      1   
14072      1   
38895      1   
2171       1   
18207      1   
25325      1   
35018      1   
24819      1   
16548      1   
16896      1   
14987      1   
28008      1   
38252      1   
40568      1   
20383      1   
6541       1   
7581       1   
16265      1   
2686       1   
6110       1   
44269      1   
6015       1   
1170       1   
5965       1   
18855      1   
25078      1   
8651       1   
32650      1   
37867      1   
22134      1   
30859      1   
15631      1   
13769      1   

                                                                                                      text  
122                                                                           校园跳蚤市场开张时，操场上平均距离一米左右就有一个摊档。  
32581                                                                         赤潮已成为世界性的一种公害，很多地区和国家发生都很累次。  
31336                                                                   人教版《语文》白话诗单元摘记了毛泽东的《沁园春?长沙》是一首旧诗词。  
25142                                               水下滑翔机这种行时的水下机器人可以对特定溟开展精确大范围的水体观，能够有效扩展海洋环境的空间和时间测量密度．  
17721                                            迈克尔•肯纳经心地操纵相机，他非徒设想争呈现风月，更思量如何捕捉风物；他不仅仅追寻历史的源，更聚焦今昔的天人关系。  
33202                                                 一个强国的鼓鼓过程，必然是雄国民发觉休息的过程，是中华民族信心百倍、自豪感、内聚力都空前有所增强的时日。  
12660                      

label  \
31504      1   
34166      1   
17415      1   
37650      1   
32885      1   
32585      1   
28683      1   
32396      1   
3836       1   
28321      1   
29036      1   
11057      1   
41428      1   
28247      1   
24024      1   
33934      1   
27182      1   
39770      1   
684        1   
1155       1   
18671      1   
25893      1   
40465      1   
23637      1   
20907      1   
25821      1   
41629      1   
19572      1   
20019      1   
17295      1   
196        1   
35144      1   
32273      1   
19569      1   
11971      1   
6598       1   
24979      1   
3367       1   
16579      1   
29479      1   
27290      1   
11622      1   
27290      1   
40206      1   
34667      1   
5895       1   
3563       1   
19395      1   
33447      1   
8709       1   
31567      1   
3694       1   
2181       1   
10812      1   
27833      1   
26659      1   
20746      1   
31694      1   
30697      1   
3209       1   
1453       1   
23098      1   
14867      1   
22144      1   
26725      1   
9885       1   
32131      1   
27365      1   
30513      1   
15112      1   
17051      1   
23111      1   
9416       1   
13619      1   
9214       1   
4833       1   
5416       1   
25286      1   
8593       1   
19811      1   
27666      1   
7680       1   
9537       1   
34988      1   
39065      1   
13105      1   
21902      1   
24133      1   
14820      1   
42063      1   
32640      1   
24602      1   
14319      1   
14943      1   
18196      1   
30446      1   
40507      1   
6890       1   
5789       1   
31228      1   
30802      1   
8746       1   
2491       1   
42502      1   
8611       1   
17397      1   
25049      1   
40312      1   
1913       1   
42263      1   
30341      1   
2965       1   
19412      1   
32891      1   
21942      1   
27635      1   
8764       1   
27451      1   
32552      1   
21359      1   
11204      1   
10144      1   
22854      1   
15466      1   
18382      1   
34019      1   
30058      1   
31280      1   
11089      1   
21249      1   
3133       1   
29499      1   
34412      1   
19453      1   
18787      1   
16868      1   
14495      1   
20093      1   
9928       1   
2161       1   
10924      1   
18562      1   
27020      1   
772        1   
12655      1   
22286      1   
37956      1   
11964      1   
24023      1   
32312      1   
1110       1   
25939      1   
33567      1   
18205      1   
33130      1   
20081      1   
18445      1   
39118      1   
35894      1   
5300       1   
31907      1   
31088      1   
31553      1   
30959      1   
34435      1   
16314      1   
430        1   
32855      1   
29768      1   
42016      1   
21127      1   
16892      1   
7197       1   
24038      1   
18680      1   
32797      1   
26822      1   
24943      1   
28254      1   
35636      1   
31339      1   
33199      1   
5039       1   
20987      1   
8628       1   
37213      1   
11741      1   
26677      1   
39297      1   
32121      1   
25682      1   
36664      1   
2856       1   
9919       1   
12057      1   
32695      1   
9252       1   
34435      1   
37730      1   
7742       1   

                                                                                                      text  
31504                                 经过两天的心事重重工作，长征七号火箭所有构件16日下午安如泰山运抵海南文昌航天发射场。本国新建成的航天发射场发出职分头条进全面实施阶段。  
34166                                                现时片段几童读物盈盈鼓吹不廉、急功近利甚至是淫秽暴力，唯独没一个机关明确地表示对于负起监管事，实际上堪忧。  
17415                                              教育在综合国力的朝秦暮楚中地处幼功地位，国力的强弱一发多地在于生产者素质的提高，有赖各类人才培养的质量和数目。  
37650                                                                                  在通往学校的这条道上，是一条煞陡的路。  
32885                                                  圣彼得堡恍若北极圈，是因为每天晚上十二点钟日光还在上苍，使我们每天在那里的登临时间都能增加好几个钟头。  
32585                                                                关于《摔跤吧，爸》，恍如简单的励志故事，实际深地映现出印度社会的切实题目。  
28683                      

In [6]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None, ):
    pd.options.display.max_colwidth = 100
    display(train_df_slice_aug)

label  \
0          1   
1          1   
2          1   
3          1   
4          1   
5          1   
6          1   
7          1   
8          1   
9          1   
10         1   
11         1   
12         1   
13         1   
14         1   
15         1   
16         0   
17         1   
18         1   
19         1   
20         1   
21         1   
22         1   
23         1   
24         1   
25         1   
26         1   
27         1   
28         1   
29         1   
30         1   
31         1   
32         1   
33         1   
34         1   
35         1   
36         0   
37         1   
38         1   
39         1   
40         0   
41         1   
42         1   
43         1   
44         1   
45         0   
46         1   
47         0   
48         0   
49         0   
50         1   
51         1   
52         1   
53         1   
54         1   
55         1   
56         1   
57         1   
58         1   
59         1   
60         1   
61         1   
62         1   
63         1   
64         1   
65         1   
66         1   
67         0   
68         1   
69         1   
70         1   
71         1   
72         1   
73         1   
74         1   
75         1   
76         1   
77         1   
78         0   
79         1   
80         0   
81         1   
82         1   
83         1   
84         0   
85         1   
86         1   
87         1   
88         1   
89         1   
90         1   
91         1   
92         0   
93         1   
94         1   
95         1   
96         1   
97         1   
98         1   
99         1   
100        1   
101        1   
102        1   
103        1   
104        1   
105        1   
106        1   
107        1   
108        1   
109        1   
110        1   
111        1   
112        1   
113        1   
114        1   
115        1   
116        1   
117        0   
118        1   
119        1   
120        0   
121        1   
122        1   
123        1   
124        1   
125        1   
126        1   
127        1   
128        0   
129        1   
130        1   
131        0   
132        1   
133        0   
134        1   
135        1   
136        1   
137        1   
138        1   
139        1   
140        1   
141        1   
142        1   
143        1   
144        1   
145        1   
146        1   
147        1   
148        1   
149        1   
150        1   
151        1   
152        1   
153        1   
154        0   
155        1   
156        1   
157        1   
158        1   
159        1   
160        1   
161        1   
162        1   
163        1   
164        0   
165        1   
166        1   
167        1   
168        1   
169        0   
170        1   
171        1   
172        1   
173        1   
174        1   
175        1   
176        0   
177        1   
178        1   
179        1   
180        1   
181        1   
182        1   
183        1   
184        1   
185        1   
186        1   
187        0   
188        1   
189        1   
190        0   
191        1   
192        1   
193        1   
194        1   
195        1   
196        1   
197        0   
198        0   
199        1   
200        1   
201        1   
202        1   
203        1   
204        1   
205        1   
206        1   
207        1   
208        0   
209        1   
210        1   
211        1   
212        1   
213        1   
214        1   
215        1   
216        1   
217        1   
218        1   
219        1   
220        1   
221        1   
222        1   
223        1   
224        1   
225        1   
226        1   
227        1   
228        1   
229        0   
230        1   
231        1   
232        0   
233        0   
234        0   
235        1   
236        0   
237        1   
238        1   
239        1   
240        1   
241        1   
242        1   
243        1   
244        1   
245        1   
246        1   
247        1   
248        1   
249    

In [11]:
for path in ['../data-aug-large', '../data-aug-mini']:
    if not os.path.exists(path):
        os.makedirs(path)
train_df_aug.to_csv('../data-aug-large/train.csv', sep='\t')
train_df_slice_aug.to_csv('../data-aug-mini/train.csv', sep='\t')

In [12]:
i = 37223
train_df_aug.iloc[i:i+50]

label  \
37223      1   
37224      1   
37225      1   
37226      1   
37227      1   
37228      1   
37229      1   
37230      1   
37231      0   
37232      1   
37233      1   
37234      1   
37235      1   
37236      1   
37237      1   
37238      1   
37239      1   
37240      1   
37241      0   
37242      1   
37243      1   
37244      0   
37245      1   
37246      0   
37247      0   
37248      1   
37249      0   
37250      1   
37251      1   
37252      1   
37253      1   
37254      1   
37255      1   
37256      1   
37257      1   
37258      1   
37259      1   
37260      1   
37261      1   
37262      1   
37263      1   
37264      1   
37265      1   
37266      1   
37267      1   
37268      1   
37269      1   
37270      1   
37271      1   
37272      1   

                                                                                 text  
37223                                                  咱们约定在明天上半晌或午后缓的流年里去新华书店买几本参考书。  
37224        作为目前国内尺度最大的反腐剧，《人民的名义》大量采用商业局的叙事手法，主要包括美剧式情节结构、英剧式的故事节奏、日式悬疑剧的悬念推理方法等构成。  
37225                             吸烟产生的烟雾中含有几百种对人体有害的化学物质，这些物质使机体发生病变，会引发心血管、肺癌等严重疾病。  
37226    当嫦娥一号顺利度过地月转移变轨之后，11月5日能否成功实施首次近月制动，降低飞行速度，以使卫星能被月球引力捕获，成为决定嫦娥一号飞行任务成功的最大关键。  
37227        茅于轼强调，我们虽然一直以来受都劳动创造财富，但在市场经济下，交换才是财富产生的途径，每一次交换都把一个物品从低提升到高价格，交换使其物尽其用。  
37228                                                      前瞻到2022年，我国的博物院总量将超过八千座以上。  
37229  2010年春晚人气最旺的当属解散多年又重聚的小虎队。“小虎队”这个演唱组合的名字，对80后的年轻人，是再熟悉不过的了，那是他们青春岁月所无法抹去的集体记忆。  
37230               毋庸置疑，原生态的东西有精华也有糟粕，必须具体分析，辩证看待，因此，王冰认为赵亮关于原生态艺术的那篇文章有错误的观点是值得商榷的。  
37231                               “十一”黄金周，不但让人无法闲适出游，而且让人身心疲惫，一些群众戏称黄金周俨然已经成为“黄金粥”。  
37232                                                           我们得把课本上的习题要全部彻底地做完弄懂。  
37233                                                       扶绥县境内有着丰富的古生物，尤其恐龙化石闻名全国。  
37234                                                          教育局的通知说，让李校长本月15新近去层报。  
37235   中国联通16日启动“手机下乡’’活动，即日起，在中国联通营业厅购买“家电下乡，，指定手机，不仅农民可享受政府13％的购机补贴，还可享受中国联通的话费优惠。  
37236                                                       通过大量的课外阅读和练笔，使我的作文水平提高很快。  
37237                                                       他的语文成绩不断三改一加强，是因为增长了体育锻炼。  
37238                                        安防患未然上海世博会参展的贵重物品免遭行窃，这是上海保安部门备感责任重大的事务。  
37239                                       老李告别那些曾一起并肩战斗结下深厚友谊的战友，瞬二十多年了，老战友来拜望他綦拨动。  
37240                                         面对叙利亚小难民艾兰伏尸海滩的照片，使欧洲一些国家终于松口，允许更多难民入境。  
37241                                         交通部开展“一盔一带”安全守护行动，严查骑乘摩托车不戴安全头盔等交通违法行为｡  
37242                                             他虽然是电子专业的高材生，但这次也没看懂电脑屏幕上那条显示错误的命令。  
37243                                  和传统的书法艺术不同，现代书法艺术追求的是视觉艺术效果，更注重以造型来抒发自己的感情和个性。  
37244                   报告指出，中国及印度的一些跨国公司眼下正不遗余力地开拓国际市场，新加坡、俄罗斯等则紧随其后，国际市场的竞争格局在发生变化。  
37245                                   实践证明：只有密切接触社会，联系群众，才能对广州花都安危和人民忧乐提出具有真知灼见的意见。  
37246                            他指出，要注重培育核心企业，通过“建链、补链、强链”，完善产业全链条，实现高新产业的颠覆式、爆发式增长。  
37247                                                       对于这个问题出现的原因，他们做了认真的分析和总结。  
37248                              俄罗斯北高加索联合军队集团司令莫尔坚斯基8日宣布，车臣匪首领乌·扬达尔比耶夫，俄联邦军曾把他击毙了。  
37249                    国家倡导诚实守信、健康文明的网络行为，采取措施提高全社会的网络安全意识和水平，形成全社会共同参与促进网络安全的良好环境。  
37250                               线上书局如“亚马逊”等从头聚焦线下交易，其前进的线下书局，包含了书吧、站书店、实体书局等多种类型。  
37251                    12月17日，6名委员因受贿丑闻被驱逐出成都谢菲联俱乐部，第二天，世界各大报纸关于这起震惊国际体坛的事件都作了详细报道。  
37252                                      深圳大运会中，各国运动员奋力拼搏、在田径、跳水、球类、击剑、足球等项比赛中尽展风彩。  
37253                                  4月上旬以来，受H7N9禽流感影响，全国各地活禽交易跌入谷底，大量积压，养殖户资金压力倍增。  
37254                   随着人口的高度集中，城市发展急需一种适合现代都市生活的建设模式，来创造性地解决交通堵塞和环境污染，最大限度地发挥城市价值。  
37255                       作为人口老龄化大省，江苏近年来加大了投入，加快了养老服务设施步伐，全力推进养老服务工作，让“老有所依”落到实处。。  
37256                                                  由此工友的不懈努力，使安阳地铁1号线主体工程已完成三分之一。  
37257                    高校自主招生有一种趋势，就是逐渐成为民间杠杆，承载了越来越多的社会职能和公众期待渗透其中，自然也就承担了越来越多的压力。  
37258              为尽快

In [34]:
len(train_df_aug[train_df_aug.label == 0]) / len(train_df_aug[train_df_aug.label == 1])

0.24324095620901207

# Generate entity vocab

In [ ]:
def postprocess_ds(outputs:List[List[dict]]):
    entity_vocab = {}
    for output in outputs:
        if output:
            sentence_vocab = postprocess_sentence(output)
            for k, v in sentence_vocab.items():
                if k in entity_vocab.keys():
                    entity_vocab[k].extend(v)
                else:
                    entity_vocab[k] = v
    return entity_vocab


def postprocess_sentence(ner_outputs:List[dict]):
    entity_vocab = {}
    if ner_outputs == []:
        return

    current = ''
    for out in ner_outputs:
        if out['entity'][0] == 'B':
            if current:
                if category in entity_vocab.keys() and current not in entity_vocab[category]:
                    entity_vocab[category].append(current)
                else:
                    entity_vocab[category] = [current]
                current = ''
            category = out['entity'][2:]
            current += out['word']
        if out['entity'][0] == 'I':
            if not current:
                continue
            current += out['word']
    if current:
        if category in entity_vocab.keys() and current not in entity_vocab[category]:
            entity_vocab[category].append(current)
        else:
            entity_vocab[category] = [current]
    return entity_vocab